In [ ]:
# download the stl files, unzip and adjust the path
# https://github.com/schiele/openscad-ldraw/releases
stl_folder='stl-LDraw-2025-10'

In [2]:
import numpy as np
import trimesh
from pathlib import Path
import plotly.graph_objects as go

# --- 1. Comprehensive LDraw Color Palette ---
# Sourced from: https://www.ldraw.org/article/547.html
LD_COLORS = {
    # Standard Solid Colors
    0:  '#05131D', # Black
    1:  '#0055BF', # Blue
    2:  '#237841', # Green
    3:  '#008F9B', # Dark Turquoise
    4:  '#C91A09', # Red
    5:  '#C870A0', # Dark Pink
    6:  '#583927', # Brown
    7:  '#9BA19D', # Light Gray
    8:  '#6D6E5C', # Dark Gray
    9:  '#B4D2E3', # Light Blue
    10: '#4B9F4A', # Bright Green
    11: '#55A5AF', # Light Turquoise
    12: '#F2705E', # Salmon
    13: '#FC97AC', # Pink
    14: '#F2CD37', # Yellow
    15: '#FFFFFF', # White
    17: '#C2DAB8', # Light Green
    18: '#FBE696', # Light Yellow
    19: '#E4CD9E', # Tan
    20: '#C9CAE2', # Light Violet
    21: '#D0D1C4', # Glow In Dark Opaque
    22: '#652073', # Purple
    23: '#1B2A34', # Dark Blue-Violet
    25: '#D67523', # Orange
    26: '#A83D15', # Magenta
    27: '#95B90B', # Lime
    28: '#F49B00', # Dark Tan
    29: '#DF6695', # Bright Pink
    30: '#6841EA', # Medium Lavender
    31: '#CDD6DA', # Lavender
    68: '#F3C988', # Very Light Orange
    69: '#96709F', # Bright Purple
    70: '#D58146', # Reddish Brown
    71: '#A0A5A9', # Light Bluish Gray
    72: '#6C6E68', # Dark Bluish Gray
    73: '#6D6E5C', # Medium Blue
    74: '#5A93DB', # Medium Green
    77: '#F3C305', # Light Pink
    78: '#F0C4A0', # Light Flesh
    84: '#AA7D55', # Medium Nougat
    85: '#4C61DB', # Medium Lilac
    86: '#7C5C85', # Dark Flesh
    89: '#2C1577', # Royal Blue
    92: '#D09168', # Flesh
    100: '#FECCCF',# Light Salmon
    110: '#4354A3', # Violet
    112: '#6874CA', # Medium Bluish Violet
    115: '#C7D23C', # Medium Lime
    118: '#B3D7D1', # Aqua
    120: '#D7C599', # Light Nougat
    125: '#F9A777', # Light Orange
    151: '#5F8265', # Very Light Bluish Gray
    191: '#F4F4F4', # Bright Light Orange
    212: '#B0A06F', # Bright Light Blue
    216: '#EAB892', # Rust
    272: '#0D325B', # Dark Blue
    288: '#184632', # Dark Green
    308: '#352100', # Dark Brown
    313: '#829004', # Maersk Blue
    320: '#720E0F', # Dark Red
    321: '#372100', # Dark Azure
    322: '#364F9E', # Medium Azure
    323: '#AEE9EF', # Light Aqua
    326: '#F3C988', # Yellowish Green
    330: '#9B9A5A', # Olive Green
    335: '#D67923', # Sand Red
    353: '#F785B1', # Coral
    366: '#AD6140', # Earth Orange
    373: '#8D7452', # Sand Purple
    378: '#B5766F', # Sand Green
    379: '#70816C', # Sand Blue
    450: '#E7F2A7', # Fabuland Brown
    462: '#C7871E', # Medium Orange
    484: '#A0654E', # Dark Orange
    503: '#E6E3DA', # Very Light Gray
    
    # Transparent Colors
    33: '#0020A0', # Trans-Dark Blue
    34: '#237841', # Trans-Green
    35: '#D67523', # Trans-Bright Green
    36: '#C91A09', # Trans-Red
    37: '#635F52', # Trans-Black (Smoke)
    38: '#A08000', # Trans-Neon Orange
    39: '#C1DFF0', # Trans-Neon Yellow
    40: '#635F52', # Trans-Very Dark Gray
    41: '#55A5AF', # Trans-Cyan
    42: '#B4D2E3', # Trans-Light Blue
    43: '#4B9F4A', # Trans-Neon Green
    44: '#96709F', # Trans-Purple
    45: '#DF6695', # Trans-Pink
    46: '#F2CD37', # Trans-Yellow
    47: '#FCFCFC', # Trans-Clear
    52: '#D0D1C4', # Trans-Glow In Dark
    54: '#F0C4A0', # Trans-Light Orange
    57: '#F2705E', # Trans-Orange

    # Chrome & Metallic
    80: '#A5A5CB', # Chrome Antique Brass
    81: '#6C6E68', # Chrome Gold
    82: '#E0E0E0', # Chrome Silver
    83: '#1B2A34', # Pearl White
    134: '#9C6106', # Pearl Copper
    135: '#958A73', # Pearl Gray
    137: '#E0E0E0', # Pearl Light Gray
    142: '#CFE2F7', # Pearl Gold
    148: '#575857', # Pearl Dark Gray
    178: '#B48455', # Flat Dark Gold
    179: '#898788', # Flat Silver
    183: '#D7D7D7', # Pearl White
    294: '#D0D1C4', # Glow In Dark Trans
    297: '#AA7F2E', # Pearl Gold (Legacy)
    
    # Special
    16: '#333333', # Main Colour (Implicit - handled by recursion normally)
    24: '#7F7F7F', # Edge Colour
}

class LDrawViewer:
    def __init__(self, mpd_file, stl_folder=stl_folder):
        self.mpd_file = Path(mpd_file)
        self.stl_folder = Path(stl_folder)
        self.parts = []
        self.library = {}
        self.scale = 0.4  # LDraw to mm scale

        # 1. Fix individual STLs: Rotate +90 on X
        self.fix_matrix = np.array([
            [1, 0, 0, 0], [0, 0, -1, 0], [0, 1, 0, 0], [0, 0, 0, 1]
        ])
        
        # 2. Fix Global Scene: Rotate -90 on X (Convert LDraw Y-down to Plotly Z-up)
        self.scene_matrix = np.array([
            [1, 0, 0, 0], [0, 0, 1, 0], [0, -1, 0, 0], [0, 0, 0, 1]
        ])

        self.parse_mpd()
        if self.library:
            self.resolve(list(self.library.keys())[0], np.eye(4))
            self.show()

    def parse_mpd(self):
        with open(self.mpd_file, 'r', encoding='utf-8', errors='ignore') as f:
            name, lines, capture = "main", [], False
            for line in f:
                s = line.strip()
                if s.startswith('0 FILE'):
                    if lines: self.library[name] = lines
                    name = s.split(maxsplit=2)[2].lower()
                    lines, capture = [], True
                elif s.startswith('0 NOFILE'):
                    self.library[name] = lines
                    lines, capture = [], False
                elif capture or (not capture and s):
                    lines.append(s)
            if lines: self.library[name] = lines

    def resolve(self, name, parent_tf):
        if name.lower() not in self.library: return
        for line in self.library[name.lower()]:
            if line.startswith('1 '):
                p = line.split()
                if len(p) < 15: continue
                try:
                    # Apply scale to XYZ translation only
                    x, y, z = float(p[2])*self.scale, float(p[3])*self.scale, float(p[4])*self.scale
                    # LDraw Matrix
                    local_tf = np.array([
                        [float(p[5]), float(p[6]), float(p[7]), x],
                        [float(p[8]), float(p[9]), float(p[10]), y],
                        [float(p[11]), float(p[12]), float(p[13]), z],
                        [0, 0, 0, 1]
                    ])
                    global_tf = parent_tf @ local_tf
                    target = " ".join(p[14:]).lower()

                    if target in self.library:
                        self.resolve(target, global_tf)
                    else:
                        self.parts.append({'file': target, 'tf': global_tf, 'c': int(p[1])})
                except ValueError: continue

    def show(self):
        fig = go.Figure()
        print(f"Rendering {len(self.parts)} parts...")
        
        for p in self.parts:
            f_name = p['file'].replace('.dat', '.stl').replace('.ldr', '.stl')
            path = self.stl_folder / f_name
            if not path.exists(): path = self.stl_folder / f_name.lower()
            if not path.exists(): continue

            try:
                mesh = trimesh.load(path, force='mesh')
                mesh.apply_transform(self.fix_matrix)   # 1. Fix STL orientation
                mesh.apply_transform(p['tf'])           # 2. Move to position
                mesh.apply_transform(self.scene_matrix) # 3. Stand model upright

                # --- UPDATED COLOR LOGIC ---
                # Default to Light Bluish Gray (71) if color not found
                c_code = p['c']
                hex_color = LD_COLORS.get(c_code, '#A0A5A9') 
                
                # Handle Transparent Colors (Opacity < 1)
                opacity = 0.5 if (33 <= c_code <= 47) or (c_code == 52) or (c_code == 57) else 1.0

                fig.add_trace(go.Mesh3d(
                    x=mesh.vertices[:,0], y=mesh.vertices[:,1], z=mesh.vertices[:,2],
                    i=mesh.faces[:,0], j=mesh.faces[:,1], k=mesh.faces[:,2],
                    color=hex_color, 
                    opacity=opacity, 
                    flatshading=True, 
                    name=f_name
                ))
            except: pass

        fig.update_layout(
            scene_aspectmode='data', 
            title="LDraw Viewer",
            scene=dict(xaxis_visible=False, yaxis_visible=False, zaxis_visible=False)
        )
        fig.show()

# Usage
# viewer = LDrawViewer('model.mpd')

In [3]:
# Load and view your MPD file
viewer = LDrawViewer('ldraw_models/8256-1.mpd')


Rendering 139 parts...
